#### Bird Species Prediction

In [1]:
import pandas as pd

#### ==>Preparing Data

##### Step 1

In [2]:
imgatt = pd.read_csv("image_attribute_labels.txt", sep="\s+", header=None,
                     usecols=[0,1,2], names=['imgid','attid','present'])
imgatt.head()

imgid  attid  present
0      1      1        0
1      1      2        0
2      1      3        0
3      1      4        0
4      1      5        1

In [3]:
imgatt.shape

(3677856, 3)

##### Step 2

In [4]:
#It has 3.7 million rows and three columns. This is not the actual formula that you want. 
#You want attributes to be the columns

imgatt2 = imgatt.pivot(index="imgid", columns="attid", values="present")
imgatt2.head()


attid  1    2    3    4    5    6    7    8    9    10   ...  303  304  305  \
imgid                                                    ...                  
1        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
2        0    0    0    0    0    0    0    0    0    0  ...    0    0    0   
3        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
4        0    0    0    0    1    0    0    0    0    0  ...    0    0    0   
5        0    0    0    0    1    0    0    0    0    0  ...    0    0    1   

attid  306  307  308  309  310  311  312  
imgid                                     
1        0    0    1    0    0    0    0  
2        0    0    0    0    0    0    0  
3        0    0    1    0    0    1    0  
4        1    0    0    1    0    0    0  
5        0    0    0    0    0    0    0  

[5 rows x 312 columns]

##### Step 3

In [5]:
#Now, we need to load the answers, such as whether it's a bird and which species it is.
#We will be using set_index('imgid') to have the same result produced by imgatt2.head()

imglabels = pd.read_csv("image_class_labels.txt", sep=' ', header=None, names=['imgid','label'] )
imglabels = imglabels.set_index('imgid')
imglabels.head()

label
imgid       
1          1
2          1
3          1
4          1
5          1

##### Step 4

In [6]:
#We will join imglabels and imgatt2 dataframes with the help of imgid

df = imgatt2.join(imglabels)
df = df.sample(frac=1)
df.head()

1  2  3  4  5  6  7  8  9  10  ...  304  305  306  307  308  309  310  \
imgid                                 ...                                      
10198  0  0  0  0  0  0  1  0  0   0  ...    0    0    0    0    1    0    0   
6733   0  0  0  0  0  0  0  1  0   0  ...    0    0    0    0    0    1    0   
1473   0  0  0  0  0  0  1  0  0   0  ...    0    0    0    1    0    0    0   
11495  0  0  0  0  0  0  1  0  0   0  ...    0    0    0    0    0    1    0   
996    0  0  0  0  0  0  0  1  0   0  ...    0    0    0    0    0    0    0   

       311  312  label  
imgid                   
10198    0    1    174  
6733     0    0    116  
1473     0    1     27  
11495    0    0    196  
996      0    0     18  

[5 rows x 313 columns]

##### Step 5

In [7]:
#Spliting off the attributes

df_att = df.iloc[:, :312]
df_label = df.iloc[:, 312:]

df_att.head()

1    2    3    4    5    6    7    8    9    10   ...  303  304  305  \
imgid                                                    ...                  
10198    0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
6733     0    0    0    0    0    0    0    1    0    0  ...    0    0    0   
1473     0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
11495    0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
996      0    0    0    0    0    0    0    1    0    0  ...    0    0    0   

       306  307  308  309  310  311  312  
imgid                                     
10198    0    0    1    0    0    0    1  
6733     0    0    0    1    0    0    0  
1473     0    1    0    0    0    0    1  
11495    0    0    0    1    0    0    0  
996      0    0    0    0    0    0    0  

[5 rows x 312 columns]

In [8]:
df_label.head()

label
imgid       
10198    174
6733     116
1473      27
11495    196
996       18

##### Step 6

In [9]:
#We will do a training test split

df_train_att = df_att[:8000]
df_train_label = df_label[:8000]

df_test_att = df_att[8000:]
df_test_label = df_label[8000:]

df_train_label = df_train_label['label']
df_test_label = df_test_label['label']

df_train_att.head()


1    2    3    4    5    6    7    8    9    10   ...  303  304  305  \
imgid                                                    ...                  
10198    0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
6733     0    0    0    0    0    0    0    1    0    0  ...    0    0    0   
1473     0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
11495    0    0    0    0    0    0    1    0    0    0  ...    0    0    0   
996      0    0    0    0    0    0    0    1    0    0  ...    0    0    0   

       306  307  308  309  310  311  312  
imgid                                     
10198    0    0    1    0    0    0    1  
6733     0    0    0    1    0    0    0  
1473     0    1    0    0    0    0    1  
11495    0    0    0    1    0    0    0  
996      0    0    0    0    0    0    0  

[5 rows x 312 columns]

#### ==>Using Forest_Random To create our model

In [18]:
from sklearn.ensemble import RandomForestClassifier
clf = RandomForestClassifier(max_features=50, random_state=0, n_estimators=100)

clf.fit(df_train_att,df_train_label)

#Let's predict a few cases

print(clf.predict(df_train_att.head()))

[174 116  27 196  18]


In [19]:

clf.score(df_test_att,df_test_label)

0.45908130939809927

In [22]:
#Let's make a confusion matrix to see which birds the dataset confuses
from sklearn.metrics import confusion_matrix
pred_label = clf.predict(df_test_att)
cm = confusion_matrix(df_test_label, pred_label)

In [23]:
cm

array([[ 5,  0,  3, ...,  0,  0,  0],
       [ 0, 11,  0, ...,  0,  1,  0],
       [ 2,  0,  8, ...,  0,  0,  0],
       ...,
       [ 0,  0,  0, ...,  2,  0,  0],
       [ 0,  0,  0, ...,  2, 10,  0],
       [ 0,  0,  0, ...,  0,  0, 15]])

In [ ]:
#Interpretation

In [ ]:
birds = pd.read_csv("classes.txt", sep='\s+', header=None, usecols=[1], names=['birdname'])
birds = birds['birdname']

In [30]:
import matplotlib.pyplot as plt
import numpy as np
def plot_conf_matric(cm, classes, normalize=False, title='Confusion Matrix', cmap=plt.cm.Blues):
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print("Confusion matrix, without normalization")
    print(cm)
    plt.imshow(cm,interpolation='nearest', cmap=cmap)
    plt.title(title)
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=90)
    plt.yticks(tick_marks, classes)
    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Prediction label')


np.set_printoptions(precision=2)
plt.figure(figsize=(60,60),dpi=300)
plot_conf_matric(cm, classes=birds, normalize=True)
# plt.show()

Normalized confusion matrix
[[0.31 0.   0.19 ... 0.   0.   0.  ]
 [0.   0.5  0.   ... 0.   0.05 0.  ]
 [0.12 0.   0.47 ... 0.   0.   0.  ]
 ...
 [0.   0.   0.   ... 0.17 0.   0.  ]
 [0.   0.   0.   ... 0.1  0.48 0.  ]
 [0.   0.   0.   ... 0.   0.   0.68]]


In [34]:
#Let's do a comparaison with other classifers

#Let's compare with the simple decision tree:
from sklearn import tree
clftree = tree.DecisionTreeClassifier()
clftree.fit(df_train_att,df_train_label)
scr = clftree.score(df_test_att,df_test_label)
print(f"Decison Tree Classifier score ==> {scr}")

Decison Tree Classifier score ==> 0.2771911298838437


In [35]:
#Let's compare with Support Vector Machine (SVM), which is the neural network approach:
from sklearn import svm
clfsvm = svm.SVC()
clfsvm.fit(df_train_att,df_train_label)
scr2 = clfsvm.score(df_test_att,df_test_label)
print(f"SVM Classifier score ==> {scr2}")

SVM Classifier score ==> 0.49208025343189016


In [ ]:
#Althought The random forest is still better 

In [36]:
#Let's perform cross-validation to make sure that we split the training test in different ways
from sklearn.model_selection import cross_val_score
scores = cross_val_score(clf,df_train_att,df_train_label,cv=5)
print("Accuracy : %0.2f(+/- %0.2f)" % (scores.mean(),scores.std()*2) )
print("#####################################################")

Accuracy : 0.43(+/- 0.02)
#####################################################


In [37]:
scoresTree = cross_val_score(clftree,df_train_att,df_train_label,cv=5)
print("Accuracy : %0.2f(+/- %0.2f)" % (scoresTree.mean(),scoresTree.std()*2) )
print("#####################################################")

Accuracy : 0.25(+/- 0.02)
#####################################################


In [38]:
scoresSVM = cross_val_score(clfsvm,df_train_att,df_train_label,cv=5)
print("Accuracy : %0.2f(+/- %0.2f)" % (scoresSVM.mean(),scoresSVM.std()*2) )
print("#####################################################")

Accuracy : 0.46(+/- 0.02)
#####################################################
